(hardware-verfication-tutorial)=

# Tutorial: Zhinst hardware verification

``````{seealso}
The complete source code of this tutorial can be found in

{nb-download}`T_verification_programs.ipynb`

``````

In [1]:
# Make output easier to read
from rich import pretty

pretty.install()

## Introduction

This tutorial gives an overview of how to use the {mod}`~quantify_scheduler.backends.zhinst_backend` for quantify-scheduler.
The example we follow in this notebook corresponds to a standard circuit QED measurement setup in which readout is performed by generating a pulse on a UFHQA, send to the device and the returning signal is measured in transmission using the same UFHQA, and an HDAWG is then used to generate the control pulses.
We set up this test setup so that it is easy to verify the hardware is behaving correctly and that it can be used for real experiments with minimal modifications.

In {ref}`how to connect <sec-zhinst-how-to-connect>` we discuss how to set up the test setup, connect all the cables, and use quantify to connect to the hardware.
In {ref}`how to configure <sec-zhinst-how-to-configure>` we discuss how to write a hardware configuration file that can be used to compile instructions for the Zurich Instruments hardware.
In {ref}`verification programs <sec-zhinst-verification-programs>` we go over how to write and compile several verification programs, how to verify that these are correct, and how to execute these on the physical hardware.

(sec-zhinst-how-to-connect)=

## How to connect

```{note}
This documentation is a work in progress. See issue #237.
Improvements to this tutorial will include adding instructions on how to connect the hardware and how to set up the initialization script as well as more example programs.
```

(sec-zhinst-how-to-configure)=

## How to create an hardware compilation configuration

``````{admonition} Example Zurich Instruments hardware compilation configuration
:class: dropdown

In this tutorial we make use of the example configuration that contains an HDAWG, a UHFQA and a few local oscillators. This configuration is fully described by the hardware compilation config file below, which contains the `"hardware_description"`, `"connectivity"`, and `"hardware_options"` information. These same files are also used for testing purposes in the CI.

```{literalinclude} ../../../../quantify_scheduler/schemas/examples/zhinst_hardware_compilation_config.json
:language: JSON
```
``````

(sec-zhinst-verification-programs)=

## Verifying the hardware compilation

`quantify-scheduler` comes with several built-in verification programs in the {mod}`~.schedules.verification` module.
Here we will start by building and compiling the first schedule by hand to show how one can construct such a schedule and debug it, before giving an overview of test programs.

### Bining and averaging - AWG staircase

#### Description
In this schedule, we will play pulses of increasing amplitude on the HDAWG.
These pulses are modulated with a local oscillator so that they appear at the same frequency as the readout pulse.
This ensures that they are visible in the acquired signal.

#### Expected outcome

One would expect to see a monotonic increase in the measured amplitude.
The actual amplitudes would probably not match the input amplitudes 1-to-1 because there is likely some loss on the signal path from the up- and down-conversion.
Additionally, depending on the overlap between the pulse and the integration window, the average measured voltage will be slightly lower, and the phase can be slightly different resulting in not all signals being in the I-quadrature.

#### Creating the staircase program

We start by manually recreating the {func}`~quantify_scheduler.schedules.verification.awg_staircase_sched`, a schedule in which (modulated) square pulses are played on an HDAWG and the UHFQA is triggered subsequently to observe the result of that schedule.

In [2]:
# import statements required to make a schedule

import numpy as np

from quantify_scheduler import Schedule
from quantify_scheduler.operations.acquisition_library import SSBIntegrationComplex
from quantify_scheduler.operations.pulse_library import IdlePulse, SquarePulse
from quantify_scheduler.resources import ClockResource



In [3]:
pulse_amps = np.linspace(0.05, 0.9, 3)
repetitions = 1024
init_duration = 4000e-6  # 4us should allow for plenty of wait time
mw_port = "q0:mw"
ro_port = "q0:res"
mw_clock = "q0.01"  # chosen to correspond to values in the hardware compilation cfg
ro_clock = "q0.ro"
readout_frequency = (
    6.5e9  # this frequency will be used for both the AWG pulse as well as
)
# for the readout.

pulse_duration = 1e-6
acq_channel = 0
integration_time = 2e-6
acquisition_delay = 0


sched = Schedule(name="AWG staircase", repetitions=repetitions)

sched.add_resource(ClockResource(name=mw_clock, freq=readout_frequency))
sched.add_resource(ClockResource(name=ro_clock, freq=readout_frequency))
pulse_amps = np.asarray(pulse_amps)


for acq_index, pulse_amp in enumerate(pulse_amps):

    sched.add(IdlePulse(duration=init_duration))

    pulse = sched.add(
        SquarePulse(
            duration=pulse_duration,
            amp=pulse_amp,
            port=mw_port,
            clock=mw_clock,
        ),
        label=f"SquarePulse_{acq_index}",
    )

    sched.add(
        SSBIntegrationComplex(
            duration=integration_time,
            port=ro_port,
            clock=ro_clock,
            acq_index=acq_index,
            acq_channel=acq_channel,
        ),
        ref_op=pulse,
        ref_pt="start",
        rel_time=acquisition_delay,
        label=f"Acquisition_{acq_index}",
    )

sched



/usr/local/lib/python3.9/site-packages/quantify_scheduler/operations/acquisition_library.py:1539: FutureWarning: Using the `acq_index` argument is deprecated. Use the `coords` argument to define arbitrary user data for the acquisition. 
  warnings.warn(


Schedule "AWG staircase" containing (7) 9  (unique) operations.

Now that we have generated the schedule we can compile it and verify if the hardware output is correct.

In [4]:
from quantify_scheduler.backends.circuit_to_device import DeviceCompilationConfig
from quantify_scheduler.backends.graph_compilation import SerialCompiler
from quantify_scheduler.device_under_test.quantum_device import QuantumDevice
from quantify_scheduler.schemas.examples import utils
from quantify_scheduler.schemas.examples.device_example_cfgs import (
    example_transmon_cfg,
)

quantum_device = QuantumDevice("DUT")

transmon_device_cfg = DeviceCompilationConfig.model_validate(example_transmon_cfg)
quantum_device.hardware_config(utils.load_json_example_scheme("zhinst_hardware_compilation_config.json"))

compiler = SerialCompiler(name="compiler")
comp_sched = compiler.compile(
    schedule=sched, config=quantum_device.generate_compilation_config()
)



##### The timing table

The {attr}`.ScheduleBase.timing_table` can be used after the absolute timing has been determined. It gives an overview of all operations in the schedule at the quantum-device level.

In [5]:
# Pandas dataframes do not render correctly in the sphinx documentation environment. See issue #238.
comp_sched.timing_table



<pandas.io.formats.style.Styler object at 0x7d90656bb310>

##### The hardware timing table

The {attr}`.CompiledSchedule.hardware_timing_table` is populated during the hardware compilation. It gives an overview of all operations in the schedule at the control-electronics layer. This means that the signals are corrected for effects such as gain and latency, and that modulations have been applied.

The "waveform_id" key can be used to find the numerical waveforms in {attr}`.CompiledSchedule.hardware_waveform_dict`.

In [6]:
comp_sched.hardware_timing_table



<pandas.io.formats.style.Styler object at 0x7d90656473a0>

##### The hardware waveform dict

In [7]:
comp_sched.hardware_waveform_dict




{
    "SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,coords=None,acq_index=*,_acq_0_sample:0.0_phase:0.0": array([ 1.        +1.j        ,  1.40883205+0.12325683j,
        1.15845593-0.81115958j, ..., -1.3660254 +0.3660254j ,
       -0.81115958+1.15845593j,  0.12325683+1.40883205j]),
    "SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',reference_magnitude=None,t0=0)_acq_0_sample:0.0_phase:0.0": array([0.04873397+0.j        , 0.04705799-0.01327714j,
       0.04217509-0.02564946j, ..., 0.03450222+0.03627381j,
       0.04223463+0.02564946j, 0.04708881+0.01327714j]),
    "SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',reference_magnitude=None,t0=0)_acq_0_sample:0.0_phase:0.0": array([0.46297273+0.j        , 0.44705092-0.1261328j ,
       0.40066333-0.24366986j, ..., 0.32777112+0.34460122j,
       0.40122896+0.24366986j, 0.44734371+0.1261328j ]),
    "SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',reference_mag

##### The compiled instructions

The compiled instructions can be found in the `compiled_instructions` of the compiled schedule.

In [8]:
comp_sched.compiled_instructions




{
    'ic_hdawg0': ZIDeviceConfig(
        name='ic_hdawg0',
        settings_builder=<quantify_scheduler.backends.zhinst.settings.ZISettingsBuilder object at 0x7d906583b3d0>,
        acq_config=None
    ),
    'generic': {
        'lo0.ch1.frequency': 6600000000.0,
        'lo0.power': 13,
        'lo1.frequency': 6300000000.0,
        'lo1.power': 16
    },
    'ic_uhfqa0': ZIDeviceConfig(
        name='ic_uhfqa0',
        settings_builder=<quantify_scheduler.backends.zhinst.settings.ZISettingsBuilder object at 0x7d906583b490>,
        acq_config=ZIAcquisitionConfig(
            n_acquisitions=3,
            resolvers={
                0: functools.partial(<function result_acquisition_resolver at 0x7d90659334c0>, result_nodes=['qas/0/result/data/0/wave', 'qas/0/result/data/1/wave'])
            },
            bin_mode=<BinMode.AVERAGE: 'average'>,
            acq_protocols={0: 'SSBIntegrationComplex'}
        )
    )
}

The settings for the Zurich Instruments instruments are stored as a {class}`~.ZIDeviceConfig`, of which the `settings_builder` contains the {class}`~.backends.zhinst.settings.ZISettingsBuilder` containing both the settings to set on all the nodes in the Zurich Instruments drivers as well as the compiled `seqc` instructions.

In [9]:
# the .as_dict method can be used to generate a "readable" overview of the settings.
hdawg_settings_dict = (
    comp_sched.compiled_instructions["ic_hdawg0"].settings_builder.build().as_dict()
)
# hdawg_settings_dict
hdawg_settings_dict




{
    'sigouts/*/on': 0,
    'awgs/*/single': 1,
    'system/awg/channelgrouping': 0,
    'awgs/0/time': 0,
    'awgs/1/time': 0,
    'awgs/2/time': 0,
    'awgs/3/time': 0,
    'sigouts/0/on': 1,
    'sigouts/1/on': 1,
    'awgs/0/outputs/0/gains/0': 1,
    'awgs/0/outputs/1/gains/1': 1,
    'sigouts/0/offset': -0.0542,
    'sigouts/1/offset': -0.0328,
    'awgs/0/commandtable/data': '{"header":{"version":"0.2","partial":false},"table":[{"index":0,"waveform":{"index":0,"length":2400}},{"index":1,"waveform":{"index":1,"length":2400}},{"index":2,"waveform":{"index":2,"length":2400}}]}',
    'awgs/0/waveform/waves/0': array([1596,    0, 1541, ...,  840, 1542,  435], dtype=int16),
    'awgs/0/waveform/waves/1': array([15170,     0, 14648, ...,  7984, 14658,  4132], dtype=int16),
    'awgs/0/waveform/waves/2': array([28743,     0, 27755, ..., 15128, 27773,  7830], dtype=int16),
    'compiler/sourcestring': {
        0: '// Generated by quantify-scheduler.\n// Variables\nvar __repetitions_

The compiler source string for each awg channel can be printed to see the instructions the ZI hardware will execute.
The clock-cycles are tracked by the assembler backend and can be compared to the hardware_timing_table.

In [10]:
awg_index = 0
print(hdawg_settings_dict["compiler/sourcestring"][awg_index])



// Generated by quantify-scheduler.
// Variables
var __repetitions__ = 1024;
wave w0 = placeholder(2400);
wave w1 = placeholder(2400);
wave w2 = placeholder(2400);

// Operations
assignWaveIndex(w0, w0, 0);
assignWaveIndex(w1, w1, 1);
assignWaveIndex(w2, w2, 2);
setTrigger(0);	//  n_instr=1
repeat(__repetitions__)
{
  setTrigger(AWG_MARKER1 + AWG_MARKER2);	//  n_instr=2
  wait(1200052);		// clock=2	 n_instr=3
  executeTableEntry(0);	// clock=1200057 pulse=0 n_instr=0
  wait(1200597);		// clock=1200057	 n_instr=3
  executeTableEntry(1);	// clock=2400657 pulse=1 n_instr=0
  wait(1200597);		// clock=2400657	 n_instr=3
  executeTableEntry(2);	// clock=3601257 pulse=2 n_instr=0
  setTrigger(0);	// clock=3601257 n_instr=1
  wait(539);		// clock=3601258, dead time to ensure total schedule duration	 n_instr=3
}



In [11]:
# the .as_dict method can be used to generate a "readable" overview of the settings.
uhfqa_settings_dict = (
    comp_sched.compiled_instructions["ic_uhfqa0"].settings_builder.build().as_dict()
)
# uhfqa_settings_dict
uhfqa_settings_dict




{
    'awgs/0/single': 1,
    'qas/0/rotations/*': (1+1j),
    'qas/0/integration/sources/*': 0,
    'sigouts/0/on': 1,
    'sigouts/1/on': 1,
    'awgs/0/time': 0,
    'qas/0/integration/weights/0/real': array([1.        , 1.40883205, 1.15845593, ..., 0.        , 0.        ,
       0.        ]),
    'qas/0/integration/weights/1/real': array([ 1.        ,  0.12325683, -0.81115958, ...,  0.        ,
        0.        ,  0.        ]),
    'qas/0/integration/weights/2/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/3/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/4/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/5/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/6/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/7/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/8/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integ

In [12]:
awg_index = 0
print(uhfqa_settings_dict["compiler/sourcestring"][awg_index])



// Generated by quantify-scheduler.
// Variables
var __repetitions__ = 1024;
wave w0 = "ic_uhfqa0_awg0_wave0";

// Operations
repeat(__repetitions__)
{
  waitDigTrigger(2, 1);	// 	// clock=0
  wait(900000);		// clock=0	 n_instr=900000
  startQA(QA_INT_ALL, true);	// clock=900000 n_instr=7
  wait(900443);		// clock=900007	 n_instr=900443
  startQA(QA_INT_ALL, true);	// clock=1800450 n_instr=7
  wait(900443);		// clock=1800457	 n_instr=900443
  startQA(QA_INT_ALL, true);	// clock=2700900 n_instr=7
}



## Verification programs

`quantify-scheduler` comes with several test programs that can be used to verify that the software and the hardware are configured and functioning correctly.
You should be able to run this notebook on your setup directly if you replace the mock_setup initialization with your initialization script.

```{note}
This documentation is a work in progress. See issue #237.
Here we provide an overview of schedules that are used to verify different kinds of functionality.
This section will be expanded to include working examples.
```

### Time trace acquisition - readout pulse

#### Description

In this experiment, a square readout pulse is applied. This pulse should be visible in the acquisition window and can be used to calibrate the timing delay of the integration window.

This experiment can be used to verify the time-trace acquisition functionality of the readout module (e.g., Qblox QRM or ZI UHFQA) is working.

#### Expected outcome

A square pulse with some modulation is visible in the integration window.

{func}`~quantify_scheduler.schedules.trace_schedules.trace_schedule`

### Time trace acquisition - two pulses

#### Description

In this experiment, a square pulse is applied to the microwave drive line. This pulse should be visible in the acquisition window and can be used to calibrate the timing delay between the readout and control pulses.

This experiment can be used to verify the time-trace acquisition functionality of the readout module (e.g., Qblox QRM or ZI UHFQA) is working in combination with the synchronization between the readout module (e.g., Qblox QRM or ZI UHFQA) and the pulse generating module (e.g., Qblox QCM or ZI HDAWG).

#### Expected outcome

A square pulse with some modulation is visible on top of a second pulse with a different modulation frequency in the integration window.

{func}`~quantify_scheduler.schedules.trace_schedules.two_tone_trace_schedule`

### Weighted integration and averaging - Heterodyne spectroscopy

#### Description

#### Expected outcome

{func}`~quantify_scheduler.schedules.spectroscopy_schedules.heterodyne_spec_sched`

### Binning and averaging - acquisition staircase

#### Description

#### Expected outcome

One would expect to see a monotonic increase in the measured amplitude.
The actual amplitudes would probably not match the input amplitudes 1-to-1 because there is likely some loss on the signal path from the up- and down-conversion.
Additionally, depending on the overlap between the pulse and the integration window, the average measured voltage will be slightly lower, and the phase can be slightly different resulting in not all signals being in the I-quadrature.

{func}`~quantify_scheduler.schedules.verification.acquisition_staircase_sched`

In [13]:
from quantify_scheduler.schedules.verification import acquisition_staircase_sched

acq_channel = 0
schedule = acquisition_staircase_sched(
    readout_pulse_amps=np.linspace(0, 1, 4),
    readout_pulse_duration=1e-6,
    readout_frequency=6e9,
    acquisition_delay=100e-9,
    integration_time=2e-6,
    port="q0:res",
    clock="q0.ro",
    repetitions=1024,
    acq_channel=acq_channel,
)


comp_sched = compiler.compile(
    schedule=schedule, config=quantum_device.generate_compilation_config()
)

comp_sched.hardware_timing_table

<pandas.io.formats.style.Styler object at 0x7d906569c670>